In [64]:
import tushare as ts
import matplotlib.pyplot as plt
import pandas as pd
import MySQLdb
import time
import datetime
import warnings
warnings.filterwarnings("ignore")
from imp import reload
import chan

In [97]:
df=pd.DataFrame(columns=['ts_code','trade_time','trade_date','high','low','open','close'])
ts_code_list=[]
trade_time_list=[]
trade_date_list=[]
high_list=[]
low_list=[]
open_list=[]
close_list=[]
base_time=datetime.datetime.now()
v=20
for i in range(60000):
    rd=random.randint(0,20)-10
    ts_code='000000.SZ'
    time_time=base_time+datetime.timedelta(minutes=i-600000)
    trade_time=time_time.strftime("%Y-%m-%d %H:%M:%S")
    trade_date=time_time.strftime("%Y-%m-%d")
    high=v if rd<=0 else v+rd
    low=v if rd>0 else v-rd
    open=v
    close=v+rd
    ts_code_list.append(ts_code)
    trade_time_list.append(trade_time)
    trade_date_list.append(trade_date)
    high_list.append(high)
    low_list.append(low)
    open_list.append(open)
    close_list.append(close)
    v=v+rd
df = pd.DataFrame({'ts_code':ts_code_list, 'trade_time':trade_time_list, 'trade_date':trade_date_list, 'high':high_list, 'low':low_list, 'open':open_list, 'close':close_list})
print('build end')
reload(chan) #重新加载外部chan.py
df=chan.build(df)
print('handle end')

ValueError: arrays must all be same length

In [98]:
ts_code_list

['0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0',
 '0',
 '.',
 'S',
 'Z',
 '0',
 '0',
 '0',
 '0',
 '0'

In [79]:
result_df=pd.DataFrame()
found_qs_count=0 #找到的趋势数
found_count=0 #符合趋势的本组中枢已找到个数
zs_no_pre=0
zs_zg_pre=0
zs_zd_pre=0    
zs_gg_pre=0
zs_dd_pre=0
zs_direction_pre=''
for n, k in df.loc[(df["line"]=='bottom') | (df["line"]=='top')].iterrows():
    #print(k.zs_no, n, zs_no_pre==0 , k.zs_no>zs_no_pre)
    if k.zs_no!=0 and (zs_no_pre==0 or k.zs_no>zs_no_pre): #新中枢
        #print(k.zs_no,"新中枢",k.zs_no,k.zs_direction)
        if found_count==0 and (k.zs_direction=='downdown' or k.zs_direction=='upup'):
            found_count=found_count+1
        else: #前面已经找到一个待确认的
            if zs_direction_pre=='downdown' and k.zs_direction=='downdown' and k.gg<zs_dd_pre: #与前面的方向一致
                found_count=found_count+1
                #print('下降趋势延申')
            elif zs_direction_pre=='upup' and k.zs_direction=='upup' and k.dd>zs_gg_pre: #与前面的方向一致
                found_count=found_count+1
                #print('上升趋势延申')
            elif k.zs_direction=='upup' or k.zs_direction=='downdown': #盘整中枢，结束
                found_count=0
                #print('×盘整中枢，重新找')
            elif zs_direction_pre!=k.zs_direction: #与前面的方向不一致，作为第一个继续往下找
                found_count=1
                #print('×与之前方向不同，作为第一个往下找')
            else: #不成趋势
                found_count=1
                #print('×条件不符合，作为第一个往下找')
            if found_count>=2: #找到两个，记录
                found_qs_count=found_qs_count+1
                result_df=result_df.append({'ts_code':k.ts_code, 'trade_time':k.zs_confirm_time, 'trade_price':k.zs_confirm_price, 'n':n, 'direction': k.zs_direction},ignore_index=True)
                print('√找到两个连续符合中枢',k.ts_code, k.zs_confirm_time, k.zs_no,'共找到：',found_qs_count)
                found_count=0
        zs_no_pre=k.zs_no
        zs_zg_pre=k.zg
        zs_zd_pre=k.zg    
        zs_gg_pre=k.gg
        zs_dd_pre=k.dd
        zs_direction_pre=k.zs_direction
    elif k.zs_no==0 and found_count>0:
        line_point=k.high if k.line=='top' else k.low
        if (zs_direction_pre=='upup' and line_point<zs_gg_pre) or (zs_direction_pre=='downdown' and line_point>zs_dd_pre): #连接线段触碰前中枢
            found_count=0
            #print('×连接不符合')

√找到两个连续符合中枢 000000.SZ 2018-09-21 12:06:08 2 共找到： 1
√找到两个连续符合中枢 000000.SZ 2018-09-29 05:01:08 22 共找到： 2
√找到两个连续符合中枢 000000.SZ 2018-10-16 01:59:08 57 共找到： 3


In [81]:
result_df.groupby('direction')['trade_price'].mean()

direction
downdown   -187.0
upup       -115.5
Name: trade_price, dtype: float64